## Data Ingestion to Vector DB pipeline

In [20]:
import os
from langchain_community.document_loaders import PyPDFLoader, PyMuPDFLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from pathlib import Path

In [21]:
### Read all the pdf's inside the directory
def process_all_pdfs(pdf_directory):
    """Process all PDF files in a directory"""
    all_documents = []
    pdf_dir = Path(pdf_directory)
    
    # Find all PDF files recursively
    pdf_files = list(pdf_dir.glob("**/*.pdf"))
    
    print(f"Found {len(pdf_files)} PDF files to process")
    
    for pdf_file in pdf_files:
        print(f"\nProcessing: {pdf_file.name}")
        try:
            loader = PyPDFLoader(str(pdf_file))
            documents = loader.load()
            
            # Add source information to metadata
            for doc in documents:
                doc.metadata['source_file'] = pdf_file.name
                doc.metadata['file_type'] = 'pdf'
            
            all_documents.extend(documents)
            print(f"  ✓ Loaded {len(documents)} pages")
            
        except Exception as e:
            print(f"  ✗ Error: {e}")
    
    print(f"\nTotal documents loaded: {len(all_documents)}")
    return all_documents

# Process all PDFs in the data directory
all_pdf_documents = process_all_pdfs("../data")

Found 16 PDF files to process

Processing: 1 bit llm.pdf
  ✓ Loaded 8 pages

Processing: A Neural Probabilistic Language Model.pdf
  ✓ Loaded 19 pages

Processing: attention is all you need Paper.pdf
  ✓ Loaded 11 pages

Processing: Bert.pdf
  ✓ Loaded 16 pages

Processing: DreamFusion.pdf
  ✓ Loaded 18 pages

Processing: Fine Grained Human Feedback.pdf
  ✓ Loaded 26 pages

Processing: Gen AI for visualization.pdf
  ✓ Loaded 74 pages

Processing: Generative AI at Work.pdf
  ✓ Loaded 106 pages

Processing: Improving alignment of dialogue agents via targeted human judgements.pdf
  ✓ Loaded 77 pages

Processing: LAMDA.pdf
  ✓ Loaded 47 pages

Processing: language_understanding_paper.pdf
  ✓ Loaded 12 pages

Processing: Parameter Efficient Fine Tuning of Large Scale Pre-Trained Language Models.pdf
  ✓ Loaded 25 pages

Processing: Reinforcement Learning with Human Feedback.pdf
  ✓ Loaded 35 pages

Processing: Ten_Natural_Language_Processing_Tasks_with_Generat.pdf
  ✓ Loaded 30 pages

Proces

In [22]:
all_pdf_documents

[Document(metadata={'producer': 'pdfTeX-1.40.25', 'creator': 'LaTeX with hyperref', 'creationdate': '2024-02-28T02:54:41+00:00', 'author': '', 'keywords': '', 'moddate': '2024-02-28T02:54:41+00:00', 'ptex.fullbanner': 'This is pdfTeX, Version 3.141592653-2.6-1.40.25 (TeX Live 2023) kpathsea version 6.3.5', 'subject': '', 'title': '', 'trapped': '/False', 'source': '..\\data\\pdf\\1 bit llm.pdf', 'total_pages': 8, 'page': 0, 'page_label': '1', 'source_file': '1 bit llm.pdf', 'file_type': 'pdf'}, page_content='The Era of 1-bit LLMs:\nAll Large Language Models are in 1.58 Bits\nShuming Ma∗ Hongyu Wang∗ Lingxiao Ma Lei Wang Wenhui Wang\nShaohan Huang Li Dong Ruiping Wang Jilong Xue Furu Wei ⋄\nhttps://aka.ms/GeneralAI\nAbstract\nRecent research, such as BitNet [WMD+23], is paving the way for a new era of 1-\nbit Large Language Models (LLMs). In this work, we introduce a 1-bit LLM variant,\nnamely BitNet b1.58, in which every single parameter (or weight) of the LLM is\nternary {-1, 0, 1}. I

In [23]:
### Text splitting get into chunks

def split_documents(documents,chunk_size=800,chunk_overlap=200):
    """Split documents into smaller chunks for better RAG performance"""
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=chunk_size,
        chunk_overlap=chunk_overlap,
        length_function=len,
        separators=["\n\n", "\n", " ", ""]
    )
    split_docs = text_splitter.split_documents(documents)
    print(f"Split {len(documents)} documents into {len(split_docs)} chunks")
    
    # Show example of a chunk
    if split_docs:
        print(f"\nExample chunk:")
        print(f"Content: {split_docs[0].page_content[:200]}...")
        print(f"Metadata: {split_docs[0].metadata}")
    
    return split_docs


In [24]:
chunks=split_documents(all_pdf_documents)
chunks

Split 618 documents into 2938 chunks

Example chunk:
Content: The Era of 1-bit LLMs:
All Large Language Models are in 1.58 Bits
Shuming Ma∗ Hongyu Wang∗ Lingxiao Ma Lei Wang Wenhui Wang
Shaohan Huang Li Dong Ruiping Wang Jilong Xue Furu Wei ⋄
https://aka.ms/Gene...
Metadata: {'producer': 'pdfTeX-1.40.25', 'creator': 'LaTeX with hyperref', 'creationdate': '2024-02-28T02:54:41+00:00', 'author': '', 'keywords': '', 'moddate': '2024-02-28T02:54:41+00:00', 'ptex.fullbanner': 'This is pdfTeX, Version 3.141592653-2.6-1.40.25 (TeX Live 2023) kpathsea version 6.3.5', 'subject': '', 'title': '', 'trapped': '/False', 'source': '..\\data\\pdf\\1 bit llm.pdf', 'total_pages': 8, 'page': 0, 'page_label': '1', 'source_file': '1 bit llm.pdf', 'file_type': 'pdf'}


[Document(metadata={'producer': 'pdfTeX-1.40.25', 'creator': 'LaTeX with hyperref', 'creationdate': '2024-02-28T02:54:41+00:00', 'author': '', 'keywords': '', 'moddate': '2024-02-28T02:54:41+00:00', 'ptex.fullbanner': 'This is pdfTeX, Version 3.141592653-2.6-1.40.25 (TeX Live 2023) kpathsea version 6.3.5', 'subject': '', 'title': '', 'trapped': '/False', 'source': '..\\data\\pdf\\1 bit llm.pdf', 'total_pages': 8, 'page': 0, 'page_label': '1', 'source_file': '1 bit llm.pdf', 'file_type': 'pdf'}, page_content='The Era of 1-bit LLMs:\nAll Large Language Models are in 1.58 Bits\nShuming Ma∗ Hongyu Wang∗ Lingxiao Ma Lei Wang Wenhui Wang\nShaohan Huang Li Dong Ruiping Wang Jilong Xue Furu Wei ⋄\nhttps://aka.ms/GeneralAI\nAbstract\nRecent research, such as BitNet [WMD+23], is paving the way for a new era of 1-\nbit Large Language Models (LLMs). In this work, we introduce a 1-bit LLM variant,\nnamely BitNet b1.58, in which every single parameter (or weight) of the LLM is\nternary {-1, 0, 1}. I

## Embeddings and vectorStoreDB

In [25]:
import numpy as np
import os
from sentence_transformers import SentenceTransformer
import chromadb # embedding model
from chromadb.config import Settings
import uuid
from typing import List, Dict, Any, Tuple
from sklearn.metrics.pairwise import cosine_similarity

In [26]:
class EmbeddingManager:
    """Handles document embedding generation using SentenceTransformer"""
    
    def __init__(self, model_name: str = "all-MiniLM-L6-v2"):  # this str converting text into vectors
        """
        Initialize the embedding manager
        
        Args:
            model_name: HuggingFace model name for sentence embeddings
        """
        self.model_name = model_name
        self.model = None
        self._load_model()

    def _load_model(self):
        """Load the SentenceTransformer model"""
        try:
            print(f"Loading embedding model: {self.model_name}")
            self.model = SentenceTransformer(self.model_name)
            print(f"Model loaded successfully. Embedding dimension: {self.model.get_sentence_embedding_dimension()}")
        except Exception as e:
            print(f"Error loading model {self.model_name}: {e}")
            raise

    def generate_embeddings(self, texts: List[str]) -> np.ndarray:
        """
        Generate embeddings for a list of texts
        
        Args:
            texts: List of text strings to embed
            
        Returns:
            numpy array of embeddings with shape (len(texts), embedding_dim)
        """
        if not self.model:
            raise ValueError("Model not loaded")
        
        print(f"Generating embeddings for {len(texts)} texts...")
        embeddings = self.model.encode(texts, show_progress_bar=True)
        print(f"Generated embeddings with shape: {embeddings.shape}")
        return embeddings


## initialize the embedding manager

embedding_manager=EmbeddingManager()
embedding_manager


Loading embedding model: all-MiniLM-L6-v2
Model loaded successfully. Embedding dimension: 384


In [27]:
class VectorStore:
    """Manages document embeddings in a ChromaDB vector store"""
    
    def __init__(self, collection_name: str = "pdf_documents", persist_directory: str = "../data/vector_store"):
        """
        Initialize the vector store
        
        Args:
            collection_name: Name of the ChromaDB collection
            persist_directory: Directory to persist the vector store
        """
        self.collection_name = collection_name
        self.persist_directory = persist_directory
        self.client = None
        self.collection = None
        self._initialize_store()

    def _initialize_store(self):
        """Initialize ChromaDB client and collection"""
        try:
            # Create persistent ChromaDB client
            os.makedirs(self.persist_directory, exist_ok=True)
            self.client = chromadb.PersistentClient(path=self.persist_directory)
            
            # Get or create collection
            self.collection = self.client.get_or_create_collection(
                name=self.collection_name,
                metadata={"description": "PDF document embeddings for RAG"}
            )
            print(f"Vector store initialized. Collection: {self.collection_name}")
            print(f"Existing documents in collection: {self.collection.count()}")
            
        except Exception as e:
            print(f"Error initializing vector store: {e}")
            raise

    def add_documents(self, documents: List[Any], embeddings: np.ndarray):
        """
        Add documents and their embeddings to the vector store
        
        Args:
            documents: List of LangChain documents
            embeddings: Corresponding embeddings for the documents
        """
        if len(documents) != len(embeddings):
            raise ValueError("Number of documents must match number of embeddings")
        
        print(f"Adding {len(documents)} documents to vector store...")
        
        # Prepare data for ChromaDB
        ids = []
        metadatas = []
        documents_text = []
        embeddings_list = []
        
        for i, (doc, embedding) in enumerate(zip(documents, embeddings)):
            # Generate unique ID
            doc_id = f"doc_{uuid.uuid4().hex[:8]}_{i}"
            ids.append(doc_id)
            
            # Prepare metadata
            metadata = dict(doc.metadata)
            metadata['doc_index'] = i
            metadata['content_length'] = len(doc.page_content)
            metadatas.append(metadata)
            
            # Document content
            documents_text.append(doc.page_content)
            
            # Embedding
            embeddings_list.append(embedding.tolist())
        
        # Add to collection
        try:
            self.collection.add(
                ids=ids,
                embeddings=embeddings_list,
                metadatas=metadatas,
                documents=documents_text
            )
            print(f"Successfully added {len(documents)} documents to vector store")
            print(f"Total documents in collection: {self.collection.count()}")
            
        except Exception as e:
            print(f"Error adding documents to vector store: {e}")
            raise

vectorstore=VectorStore()
vectorstore
    

Vector store initialized. Collection: pdf_documents
Existing documents in collection: 3081


In [28]:
chunks

[Document(metadata={'producer': 'pdfTeX-1.40.25', 'creator': 'LaTeX with hyperref', 'creationdate': '2024-02-28T02:54:41+00:00', 'author': '', 'keywords': '', 'moddate': '2024-02-28T02:54:41+00:00', 'ptex.fullbanner': 'This is pdfTeX, Version 3.141592653-2.6-1.40.25 (TeX Live 2023) kpathsea version 6.3.5', 'subject': '', 'title': '', 'trapped': '/False', 'source': '..\\data\\pdf\\1 bit llm.pdf', 'total_pages': 8, 'page': 0, 'page_label': '1', 'source_file': '1 bit llm.pdf', 'file_type': 'pdf'}, page_content='The Era of 1-bit LLMs:\nAll Large Language Models are in 1.58 Bits\nShuming Ma∗ Hongyu Wang∗ Lingxiao Ma Lei Wang Wenhui Wang\nShaohan Huang Li Dong Ruiping Wang Jilong Xue Furu Wei ⋄\nhttps://aka.ms/GeneralAI\nAbstract\nRecent research, such as BitNet [WMD+23], is paving the way for a new era of 1-\nbit Large Language Models (LLMs). In this work, we introduce a 1-bit LLM variant,\nnamely BitNet b1.58, in which every single parameter (or weight) of the LLM is\nternary {-1, 0, 1}. I

In [29]:
### Convert the text to embeddings
texts=[doc.page_content for doc in chunks]

## Generate the Embeddings

embeddings=embedding_manager.generate_embeddings(texts)

##store int he vector dtaabase
vectorstore.add_documents(chunks,embeddings)

Generating embeddings for 2938 texts...


Batches: 100%|██████████| 92/92 [02:12<00:00,  1.44s/it]


Generated embeddings with shape: (2938, 384)
Adding 2938 documents to vector store...
Successfully added 2938 documents to vector store
Total documents in collection: 6019


### Retriever Pipeline From VectorStore


In [30]:
class RAGRetriever:
    """Handles query-based retrieval from the vector store"""
    
    def __init__(self, vector_store: VectorStore, embedding_manager: EmbeddingManager):
        """
        Initialize the retriever
        
        Args:
            vector_store: Vector store containing document embeddings
            embedding_manager: Manager for generating query embeddings
        """
        self.vector_store = vector_store
        self.embedding_manager = embedding_manager

    def retrieve(self, query: str, top_k: int = 5, score_threshold: float = 0.0) -> List[Dict[str, Any]]:
        """
        Retrieve relevant documents for a query
        
        Args:
            query: The search query
            top_k: Number of top results to return
            score_threshold: Minimum similarity score threshold
            
        Returns:
            List of dictionaries containing retrieved documents and metadata
        """
        print(f"Retrieving documents for query: '{query}'")
        print(f"Top K: {top_k}, Score threshold: {score_threshold}")
        
        # Generate query embedding
        query_embedding = self.embedding_manager.generate_embeddings([query])[0]
        
        # Search in vector store
        try:
            results = self.vector_store.collection.query(
                query_embeddings=[query_embedding.tolist()],
                n_results=top_k
            )
            
            # Process results
            retrieved_docs = []
            
            if results['documents'] and results['documents'][0]:
                documents = results['documents'][0]
                metadatas = results['metadatas'][0]
                distances = results['distances'][0]
                ids = results['ids'][0]
                
                for i, (doc_id, document, metadata, distance) in enumerate(zip(ids, documents, metadatas, distances)):
                    # Convert distance to similarity score (ChromaDB uses cosine distance)
                    similarity_score = 1 - distance
                    
                    if similarity_score >= score_threshold:
                        retrieved_docs.append({
                            'id': doc_id,
                            'content': document,
                            'metadata': metadata,
                            'similarity_score': similarity_score,
                            'distance': distance,
                            'rank': i + 1
                        })
                
                print(f"Retrieved {len(retrieved_docs)} documents (after filtering)")
            else:
                print("No documents found")
            
            return retrieved_docs
            
        except Exception as e:
            print(f"Error during retrieval: {e}")
            return []

rag_retriever=RAGRetriever(vectorstore,embedding_manager)



In [31]:
# rag_retriever.retrieve("Tell me about 1 bit model")

### RAG Pipeline- VectorDB To LLM Output Generation

In [32]:
import os
from dotenv import load_dotenv
load_dotenv()

print(os.getenv("GROQ_API_KEY"))

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


In [33]:
from langchain_groq import ChatGroq
from langchain_core.prompts import PromptTemplate
from langchain_core.messages import HumanMessage, SystemMessage


In [34]:
class GroqLLM:
    def __init__(self, model_name: str = "llama-3.1-8b-instant", api_key: str =None):
        """
        Initialize Groq LLM
        
        Args:
            model_name: Groq model name (qwen2-72b-instruct, llama3-70b-8192, etc.)
            api_key: Groq API key (or set GROQ_API_KEY environment variable)
        """
        self.model_name = model_name
        self.api_key = api_key or os.environ.get("GROQ_API_KEY")
        
        if not self.api_key:
            raise ValueError("Groq API key is required. Set GROQ_API_KEY environment variable or pass api_key parameter.")
        
        self.llm = ChatGroq(
            groq_api_key=self.api_key,
            model_name=self.model_name,
            temperature=0.1,
            max_tokens=1024
        )
        
        print(f"Initialized Groq LLM with model: {self.model_name}")

    def generate_response(self, query: str, context: str, max_length: int = 500) -> str:
        """
        Generate response using retrieved context
        
        Args:
            query: User question
            context: Retrieved document context
            max_length: Maximum response length
            
        Returns:
            Generated response string
        """
        
        # Create prompt template
        prompt_template = PromptTemplate(
            input_variables=["context", "question"],
            template="""You are a helpful AI assistant. Use the following context to answer the question accurately and concisely.

Context:
{context}

Question: {question}

Answer: Provide a clear and informative answer based on the context above. If the context doesn't contain enough information to answer the question, say so."""
        )
        
        # Format the prompt
        formatted_prompt = prompt_template.format(context=context, question=query)
        
        try:
            # Generate response
            messages = [HumanMessage(content=formatted_prompt)]
            response = self.llm.invoke(messages)
            return response.content
            
        except Exception as e:
            return f"Error generating response: {str(e)}"
        
    def generate_response_simple(self, query: str, context: str) -> str:
        """
        Simple response generation without complex prompting
        
        Args:
            query: User question
            context: Retrieved context
            
        Returns:
            Generated response
        """
        simple_prompt = f"""Based on this context: {context}

Question: {query}

Answer:"""
        
        try:
            messages = [HumanMessage(content=simple_prompt)]
            response = self.llm.invoke(messages)
            return response.content
        except Exception as e:
            return f"Error: {str(e)}"
    


In [35]:
# Initialize Groq LLM (you'll need to set GROQ_API_KEY environment variable)
try:
    groq_llm = GroqLLM(api_key=os.getenv("GROQ_API_KEY"))
    print("Groq LLM initialized successfully!")
except ValueError as e:
    print(f"Warning: {e}")
    print("Please set your GROQ_API_KEY environment variable to use the LLM.")
    groq_llm = None

Initialized Groq LLM with model: llama-3.1-8b-instant
Groq LLM initialized successfully!


In [36]:
# ### get the context from the retriever and pass it to the LLM

# rag_retriever.retrieve("Attention all you need")

In [37]:
### Simple RAG pipeline with Groq LLM
from langchain_groq import ChatGroq
import os
from dotenv import load_dotenv
load_dotenv()

### Initialize the Groq LLM (set your GROQ_API_KEY in environment)
groq_api_key = os.getenv("GROQ_API_KEY")

llm=ChatGroq(groq_api_key=groq_api_key,model_name="llama-3.1-8b-instant",temperature=0.1,max_tokens=1024)

## 2. Simple RAG function: retrieve context + generate response
def rag_simple(query,retriever,llm,top_k=3):
    ## retriever the context
    results=retriever.retrieve(query,top_k=top_k)
    context="\n\n".join([doc['content'] for doc in results]) if results else ""
    if not context:
        return "No relevant context found to answer the question."
    
    ## generate the answwer using GROQ LLM
    prompt=(
        "Use the following context to answer the question concisely.\n"
        "Context:\n"
        "{context}\n\n"
        "Question:\n"
        "{query}\n\n"
        "Answer:"
    )
    
    response=llm.invoke([prompt.format(context=context,query=query)])
    return response.content

In [38]:
user_query = input("What is your question? ")
answer=rag_simple(user_query,rag_retriever,llm)
print(answer)

Retrieving documents for query: 'What is Diffusion models '
Top K: 3, Score threshold: 0.0
Generating embeddings for 1 texts...


Batches: 100%|██████████| 1/1 [00:00<00:00, 24.58it/s]

Generated embeddings with shape: (1, 384)
Retrieved 3 documents (after filtering)


Diffusion models are latent variable models that use a forward process to transform data into a noise schedule, and a reverse process to denoise the noise schedule back into the original data. They are learned to reverse this forward process by denoising the noise schedule into an estimate of the original data.
